In [1]:
import torch
import yaml

# Humandoid MARL
from Humanoid_MARL.envs.base_env import GymWrapper, VectorGymWrapper
from Humanoid_MARL.utils.torch_utils import save_models, load_models
from Humanoid_MARL.agent.ppo.train_torch import Agent, eval_unroll, get_agent_actions
from Humanoid_MARL.envs.torch_wrapper import TorchWrapper
from IPython.display import HTML, clear_output
from brax.io import html
import jax
from Humanoid_MARL import envs, CONFIG_AGENT
from Humanoid_MARL.utils.utils import load_reward_config
from Humanoid_MARL import CONFIG_REWARD
import mediapy as media

In [2]:
config = {
        'num_timesteps': 100_000_000,
        'eval_frequency': 10,
        'episode_length': 1000,
        'unroll_length': 10,
        'num_minibatches': 32,
        'num_update_epochs': 8,
        'discounting': 0.97,
        'learning_rate': 3e-4,
        'entropy_cost': 1e-3,
        'num_envs': 2048,
        'batch_size': 512,
        'env_name': "humanoids",
        'render' : True,
        'device' : 'cuda',
        'model_path' : "../models/20240305_085305_ppo_humanoids.pt",
        'device_idx': 1
    }


env_config = load_reward_config(CONFIG_REWARD, config['env_name'])

with open(CONFIG_AGENT, "r") as f:
        agent_config = yaml.safe_load(f)

env = envs.create(
        config['env_name'],
        auto_reset=True,
        **env_config,
    )

env = GymWrapper(env, get_jax_state=True)
env = TorchWrapper(env, device=config['device'], get_jax_state=True)

# env warmup
observation = env.reset()
action = torch.zeros(env.action_space.shape[0] * env.num_agents).to(config['device'])
env.step(action)
agents = load_models(config['model_path'], Agent, device=config['device'])
jax_states = []
num_steps = 1000

eval_reward = 0.0
episodes = torch.zeros((), device = config['device'])
for i in range(num_steps):
    print(f"{i} / {num_steps}")
    logits, action = get_agent_actions(agents, observation, env.obs_dims)
    if agent_config.get("freeze_idx"):
        action[:,agent_config.get("freeze_idx") * 17:(agent_config.get("freeze_idx") * 17) + 17] =  torch.ones_like(action[:,agent_config.get("freeze_idx") * 17:(agent_config.get("freeze_idx") * 17) + 17]) * 0.01
    jax_state, observation, reward, done, info = env.step(Agent.dist_postprocess(action[0]))
    episodes += torch.sum(done)
    jax_states.append(jax_state)
    print(f"{i} | {info} | DONE [{done}] | Reward [{reward}]")
    eval_reward += reward
print(f"Total Reward | {eval_reward / episodes}")

Unexpected exception formatting exception. Falling back to standard exception


Traceback (most recent call last):
  File "/home/alexy/.conda/envs/humanoid/lib/python3.11/site-packages/IPython/core/interactiveshell.py", line 3553, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_501575/1624626009.py", line 38, in <module>
    env.step(action)
  File "/home/alexy/Documents/Humanoid_MARL/Humanoid_MARL/envs/torch_wrapper.py", line 48, in step
    jax_state, obs, reward, done, info = super().step(action)
                                         ^^^^^^^^^^^^^^^^^^^^
  File "/home/alexy/.conda/envs/humanoid/lib/python3.11/site-packages/gym/core.py", line 319, in step
    return self.env.step(action)
           ^^^^^^^^^^^^^^^^^^^^^
  File "/home/alexy/Documents/Humanoid_MARL/Humanoid_MARL/envs/base_env.py", line 99, in step
    self._state, obs, reward, done, info = self._step(self._state, action)
                                           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/alexy/.conda/envs/humanoid/lib/python3.11/site

: 

In [ ]:

HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

: 

In [ ]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 